In [1]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
from tensorflow import keras
plt.rcParams["figure.figsize"] = (12,7)
sns.set_style("darkgrid")

# Helperfunctions for gridline plots
from helperfunctions import get_country_specific_information, get_geojson_grid, generateBaseMap, draw_grid
NY_location, L_location, NY_num, L_num = get_country_specific_information()

In [2]:
# Load data used for modelling
df = pd.read_csv("data/space_embedding_data.csv", index_col=[0])
places = pd.read_csv("data/places_final.csv")

In [3]:
places.head()

gPlusPlaceId          name  price        lat       lon    city  \
0  101742583391038750118  Carpo London    NaN  51.509499 -0.135762  London   
1  100574642292837870712  Premium Cars    NaN  51.514637 -0.064980  London   
2  105185983265572241970   eSpares Ltd    NaN  51.479416 -0.179209  London   
3  104500852703501308358     Superdrug    NaN  51.494537 -0.145769  London   
4  107519298595557659572          Kura    2.0  51.502122 -0.163029  London   

                                             address  Grid    category  
0      16 Piccadilly, London W1J 0DE, United Kingdom  L159      Retail  
1  10 Commercial Road Premium Cars First Floor, S...  L186       Other  
2  Chelsea Wharf, 15 Lots Rd, London, Chelsea SW1...   L40   Wholesale  
3  Unit 35, Victoria Railway Station, London SW1V...  L101      Retail  
4    3-4 Park Close, London SW1X 7PQ, United Kingdom  L137  Restaurant

In [4]:
# Get embeddings from model
model = keras.models.load_model("models/continuous_model")
embeddings = pd.DataFrame(model.layers[1].get_weights()[0], index=df['Grid'])

import pickle
# Save embeddings for use in Grace
with open("embeddings/cont_emb.pkl", "wb") as f:
    pickle.dump(embeddings, f)

In [5]:
embeddings.head(3)

0         1         2         3         4         5         6   \
Grid                                                                         
L0    0.001091  0.001297  0.000842 -0.001794  0.003415 -0.003326 -0.000462   
L1    0.572294 -0.959839 -0.426572  0.937521 -1.115750  1.063627  0.688900   
L10  -0.049071  0.037713 -0.017240  0.028672 -0.032671  0.010605 -0.007951   

            7         8         9         10        11  
Grid                                                    
L0    0.003105 -0.001701  0.002380 -0.002920  0.002473  
L1   -1.082502  0.818715  0.560528  1.058209 -0.848285  
L10   0.014423  0.039272  0.032083  0.018711  0.007981

In [11]:
# Assumes that user only have ratings in either London or NY
from sklearn.metrics.pairwise import cosine_similarity

def PushIndex(df):

    #0-18 = 22-40
    #19-37 = 43-61
    #38-56 = 64-82

    old_matrix = np.array([np.array([i for i in range(22,41)]) for j in range(19)])
    new_matrix = []
    col = 21

    for idx, x_i in enumerate(old_matrix):
        new_matrix.append(x_i + idx * col)

    mapping = dict(zip([i for i in range(0,21*21)], np.array(new_matrix).flatten().tolist()))
    df['new_index'] = df.clean_index.map(mapping)
    #similiarities = [1 if i in df.new_index.values else 0 for i in range(0,21*21)]
    similiarities = [df.loc[df.new_index==num]['cosine_similarity'].values[0] if num in df.new_index.values else 0 for num in range(0,21*21)]
    similiarties = [i if i>0 else 0 for i in similiarities]
    return similiarities, df



def RecommenderSystem(IDs, Ratings):

    # Define user df
    user = pd.DataFrame({'IDs':IDs, 'Rating':Ratings})
    # Save df of visited establishments
    visited = places.loc[places.gPlusPlaceId.isin(IDs)][['gPlusPlaceId','city','Grid']]
    # Add grid cell, city to user
    user = user.merge(visited, left_on='IDs', right_on='gPlusPlaceId')
    # Save location user is from
    city = user.city.unique()[0]

    # Calculate average rating for user based on average rating user have given for each grid 
    avg_grid_rating = pd.DataFrame(user.groupby('Grid').Rating.mean())
    avg_user_rating = embeddings.loc[avg_grid_rating.index].values.T @ avg_grid_rating.values

    # Calculate the cosine similiary
    recommendation = pd.DataFrame(index = [i for i in embeddings.index if city[0] not in i])
    for grid in recommendation.index:
        recommendation.loc[grid, 'cosine_similarity'] = cosine_similarity(avg_user_rating.reshape(1,-1),embeddings.loc[grid].values.reshape(1,-1))

    if city == "London":
        recommendation['clean_index'] = [int(i[2:]) for i in recommendation.index] 

    else:
        recommendation['clean_index'] = [int(i[1:]) for i in recommendation.index] 


    # Return df similiarity to other grids
    return PushIndex(recommendation) #similiarity_list #Plot(city, similiarity_list)
    

In [7]:
import json
import matplotlib as mpl
import folium

def Plot(city, similiarity_list):

    worst_region = 2

    if city == "London":
        grid = get_geojson_grid("New York", n=NY_num)
        default_location = NY_location

    else:
        grid = get_geojson_grid("London", n=L_num)
        default_location = L_location


    m =  generateBaseMap(default_location)

    for i, box in enumerate(grid):
        geo_json = json.dumps(box)

        color = plt.cm.Greens(similiarity_list[i] / worst_region)
        color = mpl.colors.to_hex(color)

        gj = folium.GeoJson(geo_json,
                            style_function=lambda feature, color=color: {
                                                                            'fillColor': color,
                                                                            'color':"grey",
                                                                            'weight': 1,
                                                                            'dashArray': '1, 1',
                                                                            'fillOpacity': 0.9,
                                                                        })

        m.add_child(gj)
    return m

In [12]:
similiarities, recommendation = RecommenderSystem(IDs, Ratings)
recommendation = recommendation.merge(places[['lat','lon','Grid']].drop_duplicates(),left_index=True, right_on="Grid")

In [30]:
#ny_df = places.loc[(places.city =='New York')]# & (places.Grid.isin(["NY2","NY21", "NY28","NY40",'NY41', 'NY42','NY43']))]
ny_df = recommendation.loc[recommendation.cosine_similarity>0]
grid = get_geojson_grid("New York", n=NY_num)
ny_map = draw_grid(grid, NY_location)

for i, row in ny_df.iterrows():
    folium.CircleMarker(location = row[['lat','lon']].values.tolist(), radius=1, fill_color="blue").add_to(ny_map)
ny_map

In [9]:
IDs = ['101742583391038750118','100574642292837870712']
Ratings = [1,5]
similiarities = RecommenderSystem(IDs, Ratings)
Plot('London',similiarities)

In [ ]:
import requests

endpoint = "https://models.platform.2021.services/seldon/spaceembeddings/dep_ID/api/v0.1/predictions"

headers = {'Grace-Client-Secret': 'c0de6747-ffb6-4023-913f-53c8222435bb'}
IDs = ['101742583391038750118','100574642292837870712']
Ratings = [4,2]
payload = {"data": {"names": ["IDs", "Ratings"],
                    "ndarray":[IDs, Ratings]}}
response = requests.post(endpoint, json = payload, headers = headers)

print(response.status_code)
print(response.json())